In [1]:
# Import the required libraries and dependencies
import os
import requests
import json
import yfinance as yf
import pandas as pd
import numpy as np
from dotenv import load_dotenv
import alpaca_trade_api as tradeapi
import hvplot.pandas
from finta import TA
from pandas.tseries.offsets import DateOffset
from sklearn.preprocessing import StandardScaler
from sklearn import svm
from sklearn.metrics import classification_report
from datetime import datetime

%matplotlib inline

In [2]:
# Load the environment variables from the .env file by calling the load_dotenv function
load_dotenv()

True

In [3]:
# Free Crypto API Call endpoint URLs for the held cryptocurrency assets
btc_url = "https://api.alternative.me/v2/ticker/Bitcoin/?convert=USD"
eth_url = "https://api.alternative.me/v2/ticker/Ethereum/?convert=USD"

In [4]:
# Using the Python requests library, make an API call to access the current price of BTC
btc_response = requests.get(btc_url).json()

# json.dumps function to review the response data from the API call
# Indent and sort_keys parameters to make the response object readable
print(json.dumps(
    btc_response,
    indent=4,
    sort_keys=True)
)


{
    "data": {
        "1": {
            "circulating_supply": 18844806,
            "id": 1,
            "last_updated": 1634335397,
            "max_supply": 21000000,
            "name": "Bitcoin",
            "quotes": {
                "USD": {
                    "market_cap": 1156944519624,
                    "percent_change_1h": -2.02905617529151,
                    "percent_change_24h": 6.08162959096924,
                    "percent_change_7d": 13.9571510712237,
                    "percentage_change_1h": -2.02905617529151,
                    "percentage_change_24h": 6.08162959096924,
                    "percentage_change_7d": 13.9571510712237,
                    "price": 61417.0,
                    "volume_24h": 52143998731
                }
            },
            "rank": 1,
            "symbol": "BTC",
            "total_supply": 18844806,
            "website_slug": "bitcoin"
        }
    },
    "metadata": {
        "error": null,
        "num_cryptocurrencies

In [5]:
# Same for ETH
eth_response = requests.get(eth_url).json()

print(json.dumps(
    eth_response,
    indent=4,
    sort_keys=True)
)

{
    "data": {
        "1027": {
            "circulating_supply": 117941792,
            "id": 1027,
            "last_updated": 1634335461,
            "max_supply": 0,
            "name": "Ethereum",
            "quotes": {
                "USD": {
                    "market_cap": 454705650576,
                    "percent_change_1h": -1.14906905317638,
                    "percent_change_24h": 1.86881495174161,
                    "percent_change_7d": 7.20430874854029,
                    "percentage_change_1h": -1.14906905317638,
                    "percentage_change_24h": 1.86881495174161,
                    "percentage_change_7d": 7.20430874854029,
                    "price": 3853.91,
                    "volume_24h": 22925864003
                }
            },
            "rank": 2,
            "symbol": "ETH",
            "total_supply": 117941792,
            "website_slug": "ethereum"
        }
    },
    "metadata": {
        "error": null,
        "num_cryptocurrenci

In [6]:
# Navigate the BTC response object to access the current price of BTC
btc_price = btc_response["data"]['1']["quotes"]["USD"]["price"]

# Print the current price of BTC
print(f"The current price for Bitcoin is ${btc_price:,}")


The current price for Bitcoin is $61,417.0


In [7]:
# Same for ETH
eth_price = eth_response["data"]['1027']["quotes"]["USD"]["price"]

print(f"""The current price for Ethereum is ${eth_price:,}
The price for 15 ETH is ${15*eth_price:,.2f}
""")

The current price for Ethereum is $3,853.91
The price for 15 ETH is $57,808.65



In [8]:
# Use yfinance to retrieve BTC and ETH close values (note that with the current API 1m data can only be done for 7 days, and 1 hour only for 730 days)

start = "2020-10-30"
end = "2021-10-14"

In [9]:
# Use yfinance to retrieve BTC and ETH close values
btc_df = yf.download(
    "BTC-USD",
    start=start,
    end=end,
    interval="1h"
)

btc_df= btc_df.rename(columns=str.lower)
btc_df= btc_df.drop(['volume','adj close'], axis=1)

btc_df

[*********************100%***********************]  1 of 1 completed


open          high           low  \
2020-10-30 07:00:00+00:00  13215.555664  13240.343750  13136.198242   
2020-10-30 08:00:00+00:00  13204.154297  13320.839844  13204.154297   
2020-10-30 09:00:00+00:00  13236.676758  13277.878906  13180.099609   
2020-10-30 10:00:00+00:00  13273.737305  13329.647461  13219.841797   
2020-10-30 11:00:00+00:00  13286.978516  13361.170898  13253.418945   
...                                 ...           ...           ...   
2021-10-14 03:00:00+01:00  58284.914062  58478.734375  58113.347656   
2021-10-14 04:00:00+01:00  58218.691406  58247.046875  58038.828125   
2021-10-14 05:00:00+01:00  58065.078125  58146.457031  57733.539062   
2021-10-14 06:00:00+01:00  57972.339844  58088.710938  57815.269531   
2021-10-14 07:00:00+01:00  57996.125000  58044.355469  57585.601562   

                                  close  
2020-10-30 07:00:00+00:00  13206.240234  
2020-10-30 08:00:00+00:00  13236.133789  
2020-10-30 09:00:00+00:00  13275.635742  
2020-10-30 10:00:00+00:00  13286.879883  
2020-10-30 11:00:00+00:00  13352.094727  
...                                 ...  
2021-10-14 03:00:00+01:00  58196.652344  
2021-10-14 04:00:00+01:00  58069.679688  
2021-10-14 05:00:00+01:00  57948.472656  
2021-10-14 06:00:00+01:00  57980.929688  
2021-10-14 07:00:00+01:00  57639.828125  

[8346 rows x 4 columns]

In [10]:
btc_df.loc[:,['close']].hvplot()

:Curve   [index]   (close)

In [11]:
# Using the Python requests library, make an API call to access the current fear and greed
fear_and_greed_url = "https://api.alternative.me/fng/?limit=350"

fear_and_greed_response = requests.get(fear_and_greed_url).json()

fear_greed_df = pd.DataFrame(fear_and_greed_response["data"])

fear_greed_df['timestamp'] = pd.to_datetime(fear_greed_df['timestamp'], unit='s')

fear_greed_df = fear_greed_df.set_index('timestamp').drop(['time_until_update', 'value_classification'], axis=1)

fear_greed_df

value
timestamp       
2021-10-15    71
2021-10-14    70
2021-10-13    70
2021-10-12    78
2021-10-11    71
...          ...
2020-11-04    74
2020-11-03    71
2020-11-02    71
2020-11-01    72
2020-10-31    73

[350 rows x 1 columns]

In [12]:
#We merge the columns

btc_df_new = btc_df.reset_index()
btc_df_new['Dates'] = pd.to_datetime(btc_df_new['index']).dt.date
btc_df_new['Time'] = pd.to_datetime(btc_df_new['index']).dt.time
btc_df_new = btc_df_new.set_index("Dates")
btc_df_new = pd.merge(btc_df_new, fear_greed_df, left_index=True, right_index=True)
btc_df_new = btc_df_new.reset_index()
btc_df_new = btc_df_new.drop(['level_0', 'Time'], axis=1)
btc_df_new = btc_df_new.set_index("index")
btc_df_new.rename({'value': 'fear_greed'}, axis=1, inplace=True)
btc_df = btc_df_new

btc_df

open          high           low  \
index                                                                 
2020-10-31 00:00:00+00:00  13546.532227  13634.988281  13526.984375   
2020-10-31 01:00:00+00:00  13614.615234  13642.466797  13579.181641   
2020-10-31 02:00:00+00:00  13628.602539  13704.597656  13577.035156   
2020-10-31 03:00:00+00:00  13593.518555  13607.653320  13462.272461   
2020-10-31 04:00:00+00:00  13481.482422  13509.704102  13457.530273   
...                                 ...           ...           ...   
2021-10-14 03:00:00+01:00  58284.914062  58478.734375  58113.347656   
2021-10-14 04:00:00+01:00  58218.691406  58247.046875  58038.828125   
2021-10-14 05:00:00+01:00  58065.078125  58146.457031  57733.539062   
2021-10-14 06:00:00+01:00  57972.339844  58088.710938  57815.269531   
2021-10-14 07:00:00+01:00  57996.125000  58044.355469  57585.601562   

                                  close fear_greed  
index                                               
2020-10-31 00:00:00+00:00  13614.940430         73  
2020-10-31 01:00:00+00:00  13628.603516         73  
2020-10-31 02:00:00+00:00  13593.518555         73  
2020-10-31 03:00:00+00:00  13481.185547         73  
2020-10-31 04:00:00+00:00  13504.777344         73  
...                                 ...        ...  
2021-10-14 03:00:00+01:00  58196.652344         70  
2021-10-14 04:00:00+01:00  58069.679688         70  
2021-10-14 05:00:00+01:00  57948.472656         70  
2021-10-14 06:00:00+01:00  57980.929688         70  
2021-10-14 07:00:00+01:00  57639.828125         70  

[8329 rows x 5 columns]

In [13]:
# We add SMA to our data, long and short to be verified

sma_short = 20
sma_long = 100

SMA20 = TA.SMA(btc_df, sma_short)
SMA100 = TA.SMA(btc_df, sma_long)

btc_df["SMA20"]=SMA20
btc_df["SMA100"]=SMA100

btc_df

open          high           low  \
index                                                                 
2020-10-31 00:00:00+00:00  13546.532227  13634.988281  13526.984375   
2020-10-31 01:00:00+00:00  13614.615234  13642.466797  13579.181641   
2020-10-31 02:00:00+00:00  13628.602539  13704.597656  13577.035156   
2020-10-31 03:00:00+00:00  13593.518555  13607.653320  13462.272461   
2020-10-31 04:00:00+00:00  13481.482422  13509.704102  13457.530273   
...                                 ...           ...           ...   
2021-10-14 03:00:00+01:00  58284.914062  58478.734375  58113.347656   
2021-10-14 04:00:00+01:00  58218.691406  58247.046875  58038.828125   
2021-10-14 05:00:00+01:00  58065.078125  58146.457031  57733.539062   
2021-10-14 06:00:00+01:00  57972.339844  58088.710938  57815.269531   
2021-10-14 07:00:00+01:00  57996.125000  58044.355469  57585.601562   

                                  close fear_greed         SMA20        SMA100  
index                                                                           
2020-10-31 00:00:00+00:00  13614.940430         73           NaN           NaN  
2020-10-31 01:00:00+00:00  13628.603516         73           NaN           NaN  
2020-10-31 02:00:00+00:00  13593.518555         73           NaN           NaN  
2020-10-31 03:00:00+00:00  13481.185547         73           NaN           NaN  
2020-10-31 04:00:00+00:00  13504.777344         73           NaN           NaN  
...                                 ...        ...           ...           ...  
2021-10-14 03:00:00+01:00  58196.652344         70  56367.859375  56207.659297  
2021-10-14 04:00:00+01:00  58069.679688         70  56531.643164  56238.673867  
2021-10-14 05:00:00+01:00  57948.472656         70  56694.410352  56268.402773  
2021-10-14 06:00:00+01:00  57980.929688         70  56847.925781  56304.039336  
2021-10-14 07:00:00+01:00  57639.828125         70  56997.965820  56333.955273  

[8329 rows x 7 columns]

In [14]:
# Create a column to hold the trading signal
btc_df["SMA Signal"] = 0.0

# Generate the trading signal 0 or 1,
# where 1 is the short-window (SMA20) greater than the long-window (SMA100)
# and 0 is when the condition is not met
btc_df['SMA Signal'] = np.where((btc_df['SMA20'] < btc_df['SMA100']),
                            1.0, 0.0)
# Review the DataFrame
btc_df

open          high           low  \
index                                                                 
2020-10-31 00:00:00+00:00  13546.532227  13634.988281  13526.984375   
2020-10-31 01:00:00+00:00  13614.615234  13642.466797  13579.181641   
2020-10-31 02:00:00+00:00  13628.602539  13704.597656  13577.035156   
2020-10-31 03:00:00+00:00  13593.518555  13607.653320  13462.272461   
2020-10-31 04:00:00+00:00  13481.482422  13509.704102  13457.530273   
...                                 ...           ...           ...   
2021-10-14 03:00:00+01:00  58284.914062  58478.734375  58113.347656   
2021-10-14 04:00:00+01:00  58218.691406  58247.046875  58038.828125   
2021-10-14 05:00:00+01:00  58065.078125  58146.457031  57733.539062   
2021-10-14 06:00:00+01:00  57972.339844  58088.710938  57815.269531   
2021-10-14 07:00:00+01:00  57996.125000  58044.355469  57585.601562   

                                  close fear_greed         SMA20  \
index                                                              
2020-10-31 00:00:00+00:00  13614.940430         73           NaN   
2020-10-31 01:00:00+00:00  13628.603516         73           NaN   
2020-10-31 02:00:00+00:00  13593.518555         73           NaN   
2020-10-31 03:00:00+00:00  13481.185547         73           NaN   
2020-10-31 04:00:00+00:00  13504.777344         73           NaN   
...                                 ...        ...           ...   
2021-10-14 03:00:00+01:00  58196.652344         70  56367.859375   
2021-10-14 04:00:00+01:00  58069.679688         70  56531.643164   
2021-10-14 05:00:00+01:00  57948.472656         70  56694.410352   
2021-10-14 06:00:00+01:00  57980.929688         70  56847.925781   
2021-10-14 07:00:00+01:00  57639.828125         70  56997.965820   

                                 SMA100  SMA Signal  
index                                                
2020-10-31 00:00:00+00:00           NaN         0.0  
2020-10-31 01:00:00+00:00           NaN         0.0  
2020-10-31 02:00:00+00:00           NaN         0.0  
2020-10-31 03:00:00+00:00           NaN         0.0  
2020-10-31 04:00:00+00:00           NaN         0.0  
...                                 ...         ...  
2021-10-14 03:00:00+01:00  56207.659297         0.0  
2021-10-14 04:00:00+01:00  56238.673867         0.0  
2021-10-14 05:00:00+01:00  56268.402773         0.0  
2021-10-14 06:00:00+01:00  56304.039336         0.0  
2021-10-14 07:00:00+01:00  56333.955273         0.0  

[8329 rows x 8 columns]

In [15]:
# Calculate the points in time when the Signal value changes
# Identify trade entry (1) and exit (-1) points
btc_df["SMA Entry/Exit"] = btc_df["SMA Signal"].diff()

# Review the DataFrame
btc_df

open          high           low  \
index                                                                 
2020-10-31 00:00:00+00:00  13546.532227  13634.988281  13526.984375   
2020-10-31 01:00:00+00:00  13614.615234  13642.466797  13579.181641   
2020-10-31 02:00:00+00:00  13628.602539  13704.597656  13577.035156   
2020-10-31 03:00:00+00:00  13593.518555  13607.653320  13462.272461   
2020-10-31 04:00:00+00:00  13481.482422  13509.704102  13457.530273   
...                                 ...           ...           ...   
2021-10-14 03:00:00+01:00  58284.914062  58478.734375  58113.347656   
2021-10-14 04:00:00+01:00  58218.691406  58247.046875  58038.828125   
2021-10-14 05:00:00+01:00  58065.078125  58146.457031  57733.539062   
2021-10-14 06:00:00+01:00  57972.339844  58088.710938  57815.269531   
2021-10-14 07:00:00+01:00  57996.125000  58044.355469  57585.601562   

                                  close fear_greed         SMA20  \
index                                                              
2020-10-31 00:00:00+00:00  13614.940430         73           NaN   
2020-10-31 01:00:00+00:00  13628.603516         73           NaN   
2020-10-31 02:00:00+00:00  13593.518555         73           NaN   
2020-10-31 03:00:00+00:00  13481.185547         73           NaN   
2020-10-31 04:00:00+00:00  13504.777344         73           NaN   
...                                 ...        ...           ...   
2021-10-14 03:00:00+01:00  58196.652344         70  56367.859375   
2021-10-14 04:00:00+01:00  58069.679688         70  56531.643164   
2021-10-14 05:00:00+01:00  57948.472656         70  56694.410352   
2021-10-14 06:00:00+01:00  57980.929688         70  56847.925781   
2021-10-14 07:00:00+01:00  57639.828125         70  56997.965820   

                                 SMA100  SMA Signal  SMA Entry/Exit  
index                                                                
2020-10-31 00:00:00+00:00           NaN         0.0             NaN  
2020-10-31 01:00:00+00:00           NaN         0.0             0.0  
2020-10-31 02:00:00+00:00           NaN         0.0             0.0  
2020-10-31 03:00:00+00:00           NaN         0.0             0.0  
2020-10-31 04:00:00+00:00           NaN         0.0             0.0  
...                                 ...         ...             ...  
2021-10-14 03:00:00+01:00  56207.659297         0.0             0.0  
2021-10-14 04:00:00+01:00  56238.673867         0.0             0.0  
2021-10-14 05:00:00+01:00  56268.402773         0.0             0.0  
2021-10-14 06:00:00+01:00  56304.039336         0.0             0.0  
2021-10-14 07:00:00+01:00  56333.955273         0.0             0.0  

[8329 rows x 9 columns]

In [16]:
# Visualize moving averages
moving_avgs = btc_df[['SMA20', 'SMA100', 'close']].hvplot(
    ylabel='Price in $',
    width=1000,
    height=400)

# Show the plot
moving_avgs

:NdOverlay   [Variable]
   :Curve   [index]   (value)

In [17]:
# Visualize exit position relative to close price
exit = btc_df[btc_df['SMA Entry/Exit'] == -1.0]['close'].hvplot.scatter(
    color='blue',
    marker='v',
    legend=False,
    ylabel='Price in $',
    width=1000,
    height=400)

# Visualize entry position relative to close price
entry = btc_df[btc_df['SMA Entry/Exit'] == 1.0]['close'].hvplot.scatter(
    color='limegreen',
     marker='^',
    legend=False,
    ylabel='Price in $',
    width=1000,
    height=400)

# Visualize close price for the investment
security_close = btc_df[['close']].hvplot(
    line_color='lightgray',
    ylabel='Price in $',
    width=1000,
    height=400)

# Visualize moving averages
moving_avgs = btc_df[['SMA20', 'SMA100']].hvplot(
    ylabel='Price in $',
    width=1000,
    height=400)

# Create the overlay plot
entry_exit_plot = security_close * moving_avgs * entry * exit

# Show the plot
entry_exit_plot.opts(
    title="BTC - SMA20, SMA100, Entry and Exit Points"
)

:Overlay
   .Curve.I          :Curve   [index]   (close)
   .NdOverlay.I      :NdOverlay   [Variable]
      :Curve   [index]   (value)
   .Scatter.Close.I  :Scatter   [index]   (close)
   .Scatter.Close.II :Scatter   [index]   (close)

In [18]:
# We add Bollinger Bands Width to our data

BBWIDTH = TA.BBWIDTH(btc_df)

btc_df["BBWIDTH"]=BBWIDTH
btc_df

open          high           low  \
index                                                                 
2020-10-31 00:00:00+00:00  13546.532227  13634.988281  13526.984375   
2020-10-31 01:00:00+00:00  13614.615234  13642.466797  13579.181641   
2020-10-31 02:00:00+00:00  13628.602539  13704.597656  13577.035156   
2020-10-31 03:00:00+00:00  13593.518555  13607.653320  13462.272461   
2020-10-31 04:00:00+00:00  13481.482422  13509.704102  13457.530273   
...                                 ...           ...           ...   
2021-10-14 03:00:00+01:00  58284.914062  58478.734375  58113.347656   
2021-10-14 04:00:00+01:00  58218.691406  58247.046875  58038.828125   
2021-10-14 05:00:00+01:00  58065.078125  58146.457031  57733.539062   
2021-10-14 06:00:00+01:00  57972.339844  58088.710938  57815.269531   
2021-10-14 07:00:00+01:00  57996.125000  58044.355469  57585.601562   

                                  close fear_greed         SMA20  \
index                                                              
2020-10-31 00:00:00+00:00  13614.940430         73           NaN   
2020-10-31 01:00:00+00:00  13628.603516         73           NaN   
2020-10-31 02:00:00+00:00  13593.518555         73           NaN   
2020-10-31 03:00:00+00:00  13481.185547         73           NaN   
2020-10-31 04:00:00+00:00  13504.777344         73           NaN   
...                                 ...        ...           ...   
2021-10-14 03:00:00+01:00  58196.652344         70  56367.859375   
2021-10-14 04:00:00+01:00  58069.679688         70  56531.643164   
2021-10-14 05:00:00+01:00  57948.472656         70  56694.410352   
2021-10-14 06:00:00+01:00  57980.929688         70  56847.925781   
2021-10-14 07:00:00+01:00  57639.828125         70  56997.965820   

                                 SMA100  SMA Signal  SMA Entry/Exit   BBWIDTH  
index                                                                          
2020-10-31 00:00:00+00:00           NaN         0.0             NaN       NaN  
2020-10-31 01:00:00+00:00           NaN         0.0             0.0       NaN  
2020-10-31 02:00:00+00:00           NaN         0.0             0.0       NaN  
2020-10-31 03:00:00+00:00           NaN         0.0             0.0       NaN  
2020-10-31 04:00:00+00:00           NaN         0.0             0.0       NaN  
...                                 ...         ...             ...       ...  
2021-10-14 03:00:00+01:00  56207.659297         0.0             0.0  0.089442  
2021-10-14 04:00:00+01:00  56238.673867         0.0             0.0  0.089009  
2021-10-14 05:00:00+01:00  56268.402773         0.0             0.0  0.085900  
2021-10-14 06:00:00+01:00  56304.039336         0.0             0.0  0.082573  
2021-10-14 07:00:00+01:00  56333.955273         0.0             0.0  0.074589  

[8329 rows x 10 columns]

In [19]:
# We add WMA to our data

WMA = TA.WMA(btc_df)

btc_df["WMA"]=WMA
btc_df

open          high           low  \
index                                                                 
2020-10-31 00:00:00+00:00  13546.532227  13634.988281  13526.984375   
2020-10-31 01:00:00+00:00  13614.615234  13642.466797  13579.181641   
2020-10-31 02:00:00+00:00  13628.602539  13704.597656  13577.035156   
2020-10-31 03:00:00+00:00  13593.518555  13607.653320  13462.272461   
2020-10-31 04:00:00+00:00  13481.482422  13509.704102  13457.530273   
...                                 ...           ...           ...   
2021-10-14 03:00:00+01:00  58284.914062  58478.734375  58113.347656   
2021-10-14 04:00:00+01:00  58218.691406  58247.046875  58038.828125   
2021-10-14 05:00:00+01:00  58065.078125  58146.457031  57733.539062   
2021-10-14 06:00:00+01:00  57972.339844  58088.710938  57815.269531   
2021-10-14 07:00:00+01:00  57996.125000  58044.355469  57585.601562   

                                  close fear_greed         SMA20  \
index                                                              
2020-10-31 00:00:00+00:00  13614.940430         73           NaN   
2020-10-31 01:00:00+00:00  13628.603516         73           NaN   
2020-10-31 02:00:00+00:00  13593.518555         73           NaN   
2020-10-31 03:00:00+00:00  13481.185547         73           NaN   
2020-10-31 04:00:00+00:00  13504.777344         73           NaN   
...                                 ...        ...           ...   
2021-10-14 03:00:00+01:00  58196.652344         70  56367.859375   
2021-10-14 04:00:00+01:00  58069.679688         70  56531.643164   
2021-10-14 05:00:00+01:00  57948.472656         70  56694.410352   
2021-10-14 06:00:00+01:00  57980.929688         70  56847.925781   
2021-10-14 07:00:00+01:00  57639.828125         70  56997.965820   

                                 SMA100  SMA Signal  SMA Entry/Exit   BBWIDTH  \
index                                                                           
2020-10-31 00:00:00+00:00           NaN         0.0             NaN       NaN   
2020-10-31 01:00:00+00:00           NaN         0.0             0.0       NaN   
2020-10-31 02:00:00+00:00           NaN         0.0             0.0       NaN   
2020-10-31 03:00:00+00:00           NaN         0.0             0.0       NaN   
2020-10-31 04:00:00+00:00           NaN         0.0             0.0       NaN   
...                                 ...         ...             ...       ...   
2021-10-14 03:00:00+01:00  56207.659297         0.0             0.0  0.089442   
2021-10-14 04:00:00+01:00  56238.673867         0.0             0.0  0.089009   
2021-10-14 05:00:00+01:00  56268.402773         0.0             0.0  0.085900   
2021-10-14 06:00:00+01:00  56304.039336         0.0             0.0  0.082573   
2021-10-14 07:00:00+01:00  56333.955273         0.0             0.0  0.074589   

                                    WMA  
index                                    
2020-10-31 00:00:00+00:00           NaN  
2020-10-31 01:00:00+00:00           NaN  
2020-10-31 02:00:00+00:00           NaN  
2020-10-31 03:00:00+00:00           NaN  
2020-10-31 04:00:00+00:00           NaN  
...                                 ...  
2021-10-14 03:00:00+01:00  57704.900694  
2021-10-14 04:00:00+01:00  57818.464757  
2021-10-14 05:00:00+01:00  57882.801302  
2021-10-14 06:00:00+01:00  57938.076302  
2021-10-14 07:00:00+01:00  57902.769531  

[8329 rows x 11 columns]

In [20]:
# Calculate the daily returns using the closing prices and the pct_change function
btc_df["actual_returns"] = btc_df["close"].pct_change()
btc_df = btc_df.dropna()

# Display sample data
btc_df

open          high           low  \
index                                                                 
2020-11-04 11:00:00+00:00  13687.083984  13732.484375  13664.735352   
2020-11-04 12:00:00+00:00  13726.798828  13818.046875  13705.649414   
2020-11-04 13:00:00+00:00  13783.478516  13878.233398  13783.478516   
2020-11-04 14:00:00+00:00  13849.971680  13849.971680  13757.506836   
2020-11-04 15:00:00+00:00  13809.415039  13912.191406  13809.415039   
...                                 ...           ...           ...   
2021-10-14 03:00:00+01:00  58284.914062  58478.734375  58113.347656   
2021-10-14 04:00:00+01:00  58218.691406  58247.046875  58038.828125   
2021-10-14 05:00:00+01:00  58065.078125  58146.457031  57733.539062   
2021-10-14 06:00:00+01:00  57972.339844  58088.710938  57815.269531   
2021-10-14 07:00:00+01:00  57996.125000  58044.355469  57585.601562   

                                  close fear_greed         SMA20  \
index                                                              
2020-11-04 11:00:00+00:00  13726.777344         74  13755.563525   
2020-11-04 12:00:00+00:00  13783.335938         74  13758.907812   
2020-11-04 13:00:00+00:00  13849.932617         74  13765.966260   
2020-11-04 14:00:00+00:00  13809.601562         74  13768.925537   
2020-11-04 15:00:00+00:00  13893.909180         74  13777.861816   
...                                 ...        ...           ...   
2021-10-14 03:00:00+01:00  58196.652344         70  56367.859375   
2021-10-14 04:00:00+01:00  58069.679688         70  56531.643164   
2021-10-14 05:00:00+01:00  57948.472656         70  56694.410352   
2021-10-14 06:00:00+01:00  57980.929688         70  56847.925781   
2021-10-14 07:00:00+01:00  57639.828125         70  56997.965820   

                                 SMA100  SMA Signal  SMA Entry/Exit   BBWIDTH  \
index                                                                           
2020-11-04 11:00:00+00:00  13665.929932         0.0             0.0  0.026101   
2020-11-04 12:00:00+00:00  13667.613887         0.0             0.0  0.026010   
2020-11-04 13:00:00+00:00  13669.827178         0.0             0.0  0.026402   
2020-11-04 14:00:00+00:00  13671.988008         0.0             0.0  0.026521   
2020-11-04 15:00:00+00:00  13676.115244         0.0             0.0  0.027420   
...                                 ...         ...             ...       ...   
2021-10-14 03:00:00+01:00  56207.659297         0.0             0.0  0.089442   
2021-10-14 04:00:00+01:00  56238.673867         0.0             0.0  0.089009   
2021-10-14 05:00:00+01:00  56268.402773         0.0             0.0  0.085900   
2021-10-14 06:00:00+01:00  56304.039336         0.0             0.0  0.082573   
2021-10-14 07:00:00+01:00  56333.955273         0.0             0.0  0.074589   

                                    WMA  actual_returns  
index                                                    
2020-11-04 11:00:00+00:00  13703.652995        0.002912  
2020-11-04 12:00:00+00:00  13712.505556        0.004120  
2020-11-04 13:00:00+00:00  13737.344076        0.004832  
2020-11-04 14:00:00+00:00  13754.929275       -0.002912  
2020-11-04 15:00:00+00:00  13788.565495        0.006105  
...                                 ...             ...  
2021-10-14 03:00:00+01:00  57704.900694       -0.001556  
2021-10-14 04:00:00+01:00  57818.464757       -0.002182  
2021-10-14 05:00:00+01:00  57882.801302       -0.002087  
2021-10-14 06:00:00+01:00  57938.076302        0.000560  
2021-10-14 07:00:00+01:00  57902.769531       -0.005883  

[8230 rows x 12 columns]

In [21]:
# Create a new column for actual returns signals
btc_df['actual returns signal'] = 0.0

# Create the signal to buy
btc_df['actual returns signal'] = np.where((btc_df['actual_returns'] < 0),
                            -1.0, 1.0)

btc_df

C:\Users\jaten\anaconda3\envs\dev\lib\site-packages\ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  
C:\Users\jaten\anaconda3\envs\dev\lib\site-packages\ipykernel_launcher.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


open          high           low  \
index                                                                 
2020-11-04 11:00:00+00:00  13687.083984  13732.484375  13664.735352   
2020-11-04 12:00:00+00:00  13726.798828  13818.046875  13705.649414   
2020-11-04 13:00:00+00:00  13783.478516  13878.233398  13783.478516   
2020-11-04 14:00:00+00:00  13849.971680  13849.971680  13757.506836   
2020-11-04 15:00:00+00:00  13809.415039  13912.191406  13809.415039   
...                                 ...           ...           ...   
2021-10-14 03:00:00+01:00  58284.914062  58478.734375  58113.347656   
2021-10-14 04:00:00+01:00  58218.691406  58247.046875  58038.828125   
2021-10-14 05:00:00+01:00  58065.078125  58146.457031  57733.539062   
2021-10-14 06:00:00+01:00  57972.339844  58088.710938  57815.269531   
2021-10-14 07:00:00+01:00  57996.125000  58044.355469  57585.601562   

                                  close fear_greed         SMA20  \
index                                                              
2020-11-04 11:00:00+00:00  13726.777344         74  13755.563525   
2020-11-04 12:00:00+00:00  13783.335938         74  13758.907812   
2020-11-04 13:00:00+00:00  13849.932617         74  13765.966260   
2020-11-04 14:00:00+00:00  13809.601562         74  13768.925537   
2020-11-04 15:00:00+00:00  13893.909180         74  13777.861816   
...                                 ...        ...           ...   
2021-10-14 03:00:00+01:00  58196.652344         70  56367.859375   
2021-10-14 04:00:00+01:00  58069.679688         70  56531.643164   
2021-10-14 05:00:00+01:00  57948.472656         70  56694.410352   
2021-10-14 06:00:00+01:00  57980.929688         70  56847.925781   
2021-10-14 07:00:00+01:00  57639.828125         70  56997.965820   

                                 SMA100  SMA Signal  SMA Entry/Exit   BBWIDTH  \
index                                                                           
2020-11-04 11:00:00+00:00  13665.929932         0.0             0.0  0.026101   
2020-11-04 12:00:00+00:00  13667.613887         0.0             0.0  0.026010   
2020-11-04 13:00:00+00:00  13669.827178         0.0             0.0  0.026402   
2020-11-04 14:00:00+00:00  13671.988008         0.0             0.0  0.026521   
2020-11-04 15:00:00+00:00  13676.115244         0.0             0.0  0.027420   
...                                 ...         ...             ...       ...   
2021-10-14 03:00:00+01:00  56207.659297         0.0             0.0  0.089442   
2021-10-14 04:00:00+01:00  56238.673867         0.0             0.0  0.089009   
2021-10-14 05:00:00+01:00  56268.402773         0.0             0.0  0.085900   
2021-10-14 06:00:00+01:00  56304.039336         0.0             0.0  0.082573   
2021-10-14 07:00:00+01:00  56333.955273         0.0             0.0  0.074589   

                                    WMA  actual_returns  actual returns signal  
index                                                                           
2020-11-04 11:00:00+00:00  13703.652995        0.002912                    1.0  
2020-11-04 12:00:00+00:00  13712.505556        0.004120                    1.0  
2020-11-04 13:00:00+00:00  13737.344076        0.004832                    1.0  
2020-11-04 14:00:00+00:00  13754.929275       -0.002912                   -1.0  
2020-11-04 15:00:00+00:00  13788.565495        0.006105                    1.0  
...                                 ...             ...                    ...  
2021-10-14 03:00:00+01:00  57704.900694       -0.001556                   -1.0  
2021-10-14 04:00:00+01:00  57818.464757       -0.002182                   -1.0  
2021-10-14 05:00:00+01:00  57882.801302       -0.002087                   -1.0  
2021-10-14 06:00:00+01:00  57938.076302        0.000560                    1.0  
2021-10-14 07:00:00+01:00  57902.769531       -0.005883                   -1.0  

[8230 rows x 13 columns]

In [22]:
# Calculate the points in time when the Signal value changes
# Identify trade entry (1) and exit (-1) points
btc_df["actual returns Entry/Exit"] = btc_df["actual returns signal"].diff()

# Review the DataFrame
btc_df

C:\Users\jaten\anaconda3\envs\dev\lib\site-packages\ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  This is separate from the ipykernel package so we can avoid doing imports until


open          high           low  \
index                                                                 
2020-11-04 11:00:00+00:00  13687.083984  13732.484375  13664.735352   
2020-11-04 12:00:00+00:00  13726.798828  13818.046875  13705.649414   
2020-11-04 13:00:00+00:00  13783.478516  13878.233398  13783.478516   
2020-11-04 14:00:00+00:00  13849.971680  13849.971680  13757.506836   
2020-11-04 15:00:00+00:00  13809.415039  13912.191406  13809.415039   
...                                 ...           ...           ...   
2021-10-14 03:00:00+01:00  58284.914062  58478.734375  58113.347656   
2021-10-14 04:00:00+01:00  58218.691406  58247.046875  58038.828125   
2021-10-14 05:00:00+01:00  58065.078125  58146.457031  57733.539062   
2021-10-14 06:00:00+01:00  57972.339844  58088.710938  57815.269531   
2021-10-14 07:00:00+01:00  57996.125000  58044.355469  57585.601562   

                                  close fear_greed         SMA20  \
index                                                              
2020-11-04 11:00:00+00:00  13726.777344         74  13755.563525   
2020-11-04 12:00:00+00:00  13783.335938         74  13758.907812   
2020-11-04 13:00:00+00:00  13849.932617         74  13765.966260   
2020-11-04 14:00:00+00:00  13809.601562         74  13768.925537   
2020-11-04 15:00:00+00:00  13893.909180         74  13777.861816   
...                                 ...        ...           ...   
2021-10-14 03:00:00+01:00  58196.652344         70  56367.859375   
2021-10-14 04:00:00+01:00  58069.679688         70  56531.643164   
2021-10-14 05:00:00+01:00  57948.472656         70  56694.410352   
2021-10-14 06:00:00+01:00  57980.929688         70  56847.925781   
2021-10-14 07:00:00+01:00  57639.828125         70  56997.965820   

                                 SMA100  SMA Signal  SMA Entry/Exit   BBWIDTH  \
index                                                                           
2020-11-04 11:00:00+00:00  13665.929932         0.0             0.0  0.026101   
2020-11-04 12:00:00+00:00  13667.613887         0.0             0.0  0.026010   
2020-11-04 13:00:00+00:00  13669.827178         0.0             0.0  0.026402   
2020-11-04 14:00:00+00:00  13671.988008         0.0             0.0  0.026521   
2020-11-04 15:00:00+00:00  13676.115244         0.0             0.0  0.027420   
...                                 ...         ...             ...       ...   
2021-10-14 03:00:00+01:00  56207.659297         0.0             0.0  0.089442   
2021-10-14 04:00:00+01:00  56238.673867         0.0             0.0  0.089009   
2021-10-14 05:00:00+01:00  56268.402773         0.0             0.0  0.085900   
2021-10-14 06:00:00+01:00  56304.039336         0.0             0.0  0.082573   
2021-10-14 07:00:00+01:00  56333.955273         0.0             0.0  0.074589   

                                    WMA  actual_returns  \
index                                                     
2020-11-04 11:00:00+00:00  13703.652995        0.002912   
2020-11-04 12:00:00+00:00  13712.505556        0.004120   
2020-11-04 13:00:00+00:00  13737.344076        0.004832   
2020-11-04 14:00:00+00:00  13754.929275       -0.002912   
2020-11-04 15:00:00+00:00  13788.565495        0.006105   
...                                 ...             ...   
2021-10-14 03:00:00+01:00  57704.900694       -0.001556   
2021-10-14 04:00:00+01:00  57818.464757       -0.002182   
2021-10-14 05:00:00+01:00  57882.801302       -0.002087   
2021-10-14 06:00:00+01:00  57938.076302        0.000560   
2021-10-14 07:00:00+01:00  57902.769531       -0.005883   

                           actual returns signal  actual returns Entry/Exit  
index                                                                        
2020-11-04 11:00:00+00:00                    1.0                        NaN  
2020-11-04 12:00:00+00:00                    1.0                        0.0  
2020-11-04 13:00:00+00:00                    1.0                        0.0  
2020-11-04 14:

In [23]:
# Assign a copy of the `sma_fast` and `sma_slow` columns to a new DataFrame called `X`
X_btc = btc_df[['close','fear_greed','WMA','BBWIDTH','SMA20','SMA100',"WMA"]].shift().dropna().copy()

# Display sample data
display(X_btc.head())
display(X_btc.tail())

close fear_greed           WMA   BBWIDTH  \
index                                                                        
2020-11-04 12:00:00+00:00  13726.777344         74  13703.652995  0.026101   
2020-11-04 13:00:00+00:00  13783.335938         74  13712.505556  0.026010   
2020-11-04 14:00:00+00:00  13849.932617         74  13737.344076  0.026402   
2020-11-04 15:00:00+00:00  13809.601562         74  13754.929275  0.026521   
2020-11-04 16:00:00+00:00  13893.909180         74  13788.565495  0.027420   

                                  SMA20        SMA100           WMA  
index                                                                
2020-11-04 12:00:00+00:00  13755.563525  13665.929932  13703.652995  
2020-11-04 13:00:00+00:00  13758.907812  13667.613887  13712.505556  
2020-11-04 14:00:00+00:00  13765.966260  13669.827178  13737.344076  
2020-11-04 15:00:00+00:00  13768.925537  13671.988008  13754.929275  
2020-11-04 16:00:00+00:00  13777.861816  13676.115244  13788.565495

close fear_greed           WMA   BBWIDTH  \
index                                                                        
2021-10-14 03:00:00+01:00  58287.371094         70  57537.383854  0.085399   
2021-10-14 04:00:00+01:00  58196.652344         70  57704.900694  0.089442   
2021-10-14 05:00:00+01:00  58069.679688         70  57818.464757  0.089009   
2021-10-14 06:00:00+01:00  57948.472656         70  57882.801302  0.085900   
2021-10-14 07:00:00+01:00  57980.929688         70  57938.076302  0.082573   

                                  SMA20        SMA100           WMA  
index                                                                
2021-10-14 03:00:00+01:00  56228.159180  56174.601836  57537.383854  
2021-10-14 04:00:00+01:00  56367.859375  56207.659297  57704.900694  
2021-10-14 05:00:00+01:00  56531.643164  56238.673867  57818.464757  
2021-10-14 06:00:00+01:00  56694.410352  56268.402773  57882.801302  
2021-10-14 07:00:00+01:00  56847.925781  56304.039336  57938.076302

In [24]:
# Copy the new "signal" column to a new Series called `y`.

y_btc = btc_df['actual returns signal'].dropna().copy()

display(y_btc.head())
display(y_btc.tail())

index
2020-11-04 11:00:00+00:00    1.0
2020-11-04 12:00:00+00:00    1.0
2020-11-04 13:00:00+00:00    1.0
2020-11-04 14:00:00+00:00   -1.0
2020-11-04 15:00:00+00:00    1.0
Name: actual returns signal, dtype: float64

index
2021-10-14 03:00:00+01:00   -1.0
2021-10-14 04:00:00+01:00   -1.0
2021-10-14 05:00:00+01:00   -1.0
2021-10-14 06:00:00+01:00    1.0
2021-10-14 07:00:00+01:00   -1.0
Name: actual returns signal, dtype: float64

In [25]:
# Select the start of the training period
training_begin = X_btc.index.min()

# Display the training begin date
print(training_begin)

# Select the ending period for the training data with an offset of 7 months
training_end = X_btc.index.min() + DateOffset(months=7)

# Display the training end date
print(training_end)

2020-11-04 12:00:00+00:00
2021-06-04 12:00:00+01:00


In [26]:
# Generate the X_train and y_train DataFrames
X_btc_train = X_btc.loc[training_begin:training_end]
y_btc_train = y_btc.loc[training_begin:training_end]

# Display sample data
display(X_btc_train.head())
display(y_btc_train.head())

close fear_greed           WMA   BBWIDTH  \
index                                                                        
2020-11-04 12:00:00+00:00  13726.777344         74  13703.652995  0.026101   
2020-11-04 13:00:00+00:00  13783.335938         74  13712.505556  0.026010   
2020-11-04 14:00:00+00:00  13849.932617         74  13737.344076  0.026402   
2020-11-04 15:00:00+00:00  13809.601562         74  13754.929275  0.026521   
2020-11-04 16:00:00+00:00  13893.909180         74  13788.565495  0.027420   

                                  SMA20        SMA100           WMA  
index                                                                
2020-11-04 12:00:00+00:00  13755.563525  13665.929932  13703.652995  
2020-11-04 13:00:00+00:00  13758.907812  13667.613887  13712.505556  
2020-11-04 14:00:00+00:00  13765.966260  13669.827178  13737.344076  
2020-11-04 15:00:00+00:00  13768.925537  13671.988008  13754.929275  
2020-11-04 16:00:00+00:00  13777.861816  13676.115244  13788.565495

index
2020-11-04 12:00:00+00:00    1.0
2020-11-04 13:00:00+00:00    1.0
2020-11-04 14:00:00+00:00   -1.0
2020-11-04 15:00:00+00:00    1.0
2020-11-04 16:00:00+00:00    1.0
Name: actual returns signal, dtype: float64

In [27]:
# Generate the X_test and y_test DataFrames
X_btc_test = X_btc.loc[training_end:]
y_btc_test = y_btc.loc[training_end:]

# Display sample data
display(X_btc_test.head())
display(y_btc_test.head())

close fear_greed           WMA   BBWIDTH  \
index                                                                        
2021-06-04 12:00:00+01:00  36678.476562         27  36873.516927  0.097004   
2021-06-04 13:00:00+01:00  36552.988281         27  36764.906076  0.101478   
2021-06-04 14:00:00+01:00  36894.601562         27  36752.502865  0.101086   
2021-06-04 15:00:00+01:00  36788.140625         27  36742.343750  0.100279   
2021-06-04 16:00:00+01:00  36735.054688         27  36741.600521  0.100218   

                                  SMA20        SMA100           WMA  
index                                                                
2021-06-04 12:00:00+01:00  37971.834570  37341.809922  36873.516927  
2021-06-04 13:00:00+01:00  37870.076367  37348.967500  36764.906076  
2021-06-04 14:00:00+01:00  37771.713086  37355.958359  36752.502865  
2021-06-04 15:00:00+01:00  37669.487695  37363.466484  36742.343750  
2021-06-04 16:00:00+01:00  37577.814063  37361.575508  36741.600521

index
2021-06-04 12:00:00+01:00   -1.0
2021-06-04 13:00:00+01:00    1.0
2021-06-04 14:00:00+01:00   -1.0
2021-06-04 15:00:00+01:00   -1.0
2021-06-04 16:00:00+01:00    1.0
Name: actual returns signal, dtype: float64

In [28]:
# Create a StandardScaler instance
scaler = StandardScaler()

# Apply the scaler model to fit the X_train data
X_btc_scaler = scaler.fit(X_btc_train)

# Transform the X_train and X_test DataFrames using the X_scaler
X_btc_train_scaled = X_btc_scaler.transform(X_btc_train)
X_btc_test_scaled = X_btc_scaler.transform(X_btc_test)

In [29]:
# Create the classifier model
svm_model = svm.SVC()

# Fit the model to the data using X_train_scaled and y_train
svm_model = svm_model.fit(X_btc_train_scaled, y_btc_train)

# Use the trained model to predict the trading signals for the training data
training_signal_predictions = svm_model.predict(X_btc_train_scaled)

# Display the sample predictions
training_signal_predictions[:10]

array([1., 1., 1., 1., 1., 1., 1., 1., 1., 1.])

In [30]:
# Evaluate the model using a classification report
training_report = classification_report(y_btc_train, training_signal_predictions)
print(training_report)

              precision    recall  f1-score   support

        -1.0       0.53      0.18      0.27      2421
         1.0       0.53      0.85      0.66      2649

    accuracy                           0.53      5070
   macro avg       0.53      0.52      0.46      5070
weighted avg       0.53      0.53      0.47      5070



In [31]:
# Use the trained model to predict the trading signals for the testing data.
testing_signal_predictions = svm_model.predict(X_btc_test_scaled)

In [32]:
# Evaluate the model's ability to predict the trading signal for the testing data
testing_report = classification_report(y_btc_test, testing_signal_predictions)
print(testing_report)

              precision    recall  f1-score   support

        -1.0       0.52      0.13      0.21      1519
         1.0       0.53      0.89      0.66      1641

    accuracy                           0.53      3160
   macro avg       0.52      0.51      0.44      3160
weighted avg       0.52      0.53      0.45      3160



In [33]:
# Create a predictions DataFrame
predictions_df = pd.DataFrame(index=X_btc_test.index)

predictions_df["predicted_signal"] = testing_signal_predictions

predictions_df["actual_returns"] = btc_df["actual_returns"]

predictions_df["trading_algorithm_returns"] = (
    predictions_df["actual_returns"] * predictions_df["predicted_signal"]
)

# Review the DataFrame
predictions_df.head(30)

predicted_signal  actual_returns  \
index                                                         
2021-06-04 12:00:00+01:00               1.0       -0.003421   
2021-06-04 13:00:00+01:00               1.0        0.009346   
2021-06-04 14:00:00+01:00               1.0       -0.002886   
2021-06-04 15:00:00+01:00               1.0       -0.001443   
2021-06-04 16:00:00+01:00               1.0        0.007629   
2021-06-04 17:00:00+01:00               1.0       -0.001986   
2021-06-04 18:00:00+01:00               1.0        0.005792   
2021-06-04 19:00:00+01:00               1.0        0.000092   
2021-06-04 20:00:00+01:00               1.0       -0.008167   
2021-06-04 21:00:00+01:00               1.0        0.005347   
2021-06-04 22:00:00+01:00               1.0        0.004168   
2021-06-04 23:00:00+01:00              -1.0       -0.001154   
2021-06-05 00:00:00+01:00              -1.0       -0.007262   
2021-06-05 01:00:00+01:00              -1.0        0.022659   
2021-06-05 02:00:00+01:00              -1.0       -0.000111   
2021-06-05 03:00:00+01:00              -1.0       -0.000354   
2021-06-05 04:00:00+01:00              -1.0       -0.007406   
2021-06-05 05:00:00+01:00              -1.0        0.006834   
2021-06-05 06:00:00+01:00              -1.0       -0.001520   
2021-06-05 07:00:00+01:00              -1.0        0.003453   
2021-06-05 08:00:00+01:00              -1.0       -0.003833   
2021-06-05 09:00:00+01:00              -1.0        0.005353   
2021-06-05 10:00:00+01:00              -1.0       -0.036409   
2021-06-05 11:00:00+01:00              -1.0        0.001334   
2021-06-05 12:00:00+01:00              -1.0       -0.013537   
2021-06-05 13:00:00+01:00               1.0        0.000485   
2021-06-05 14:00:00+01:00               1.0       -0.007315   
2021-06-05 15:00:00+01:00               1.0       -0.002834   
2021-06-05 16:00:00+01:00               1.0        0.017900   
2021-06-05 17:00:00+01:00               1.0       -0.006122   

                           trading_algorithm_returns  
index                                                 
2021-06-04 12:00:00+01:00                  -0.003421  
2021-06-04 13:00:00+01:00                   0.009346  
2021-06-04 14:00:00+01:00                  -0.002886  
2021-06-04 15:00:00+01:00                  -0.001443  
2021-06-04 16:00:00+01:00                   0.007629  
2021-06-04 17:00:00+01:00                  -0.001986  
2021-06-04 18:00:00+01:00                   0.005792  
2021-06-04 19:00:00+01:00                   0.000092  
2021-06-04 20:00:00+01:00                  -0.008167  
2021-06-04 21:00:00+01:00                   0.005347  
2021-06-04 22:00:00+01:00                   0.004168  
2021-06-04 23:00:00+01:00                   0.001154  
2021-06-05 00:00:00+01:00                   0.007262  
2021-06-05 01:00:00+01:00                  -0.022659  
2021-06-05 02:00:00+01:00                   0.000111  
2021-06-05 03:00:00+01:00                   0.000354  
2021-06-05 04:00:00+01:00                   0.007406  
2021-06-05 05:00:00+01:00                  -0.006834  
2021-06-05 06:00:00+01:00                   0.001520  
2021-06-05 07:00:00+01:00                  -0.003453  
2021-06-05 08:00:00+01:00                   0.003833  
2021-06-05 09:00:00+01:00                  -0.005353  
2021-06-05 10:00:00+01:00                   0.036409  
2021-06-05 11:00:00+01:00                  -0.001334  
2021-06-05 12:00:00+01:00                   0.013537  
2021-06-05 13:00:00+01:00                   0.000485  
2021-06-05 14:00:00+01:00                  -0.007315  
2021-06-05 15:00:00+01:00                  -0.002834  
2021-06-05 16:00:00+01:00                   0.017900  
2021-06-05 17:00:00+01:00                  -0.006122

In [34]:
# Calculate and plot the cumulative returns for the `actual_returns` and the `trading_algorithm_returns`
(1 + predictions_df[["actual_returns", "trading_algorithm_returns"]]).cumprod().hvplot()

:NdOverlay   [Variable]
   :Curve   [index]   (value)